In [1]:
import pandas as pd
import csv
import os
import re
import spacy
import pickle
import stanza
from tqdm import tqdm

In [2]:
wind = pd.read_csv('acter_wind_relative-all.csv', delimiter = '\t', header = None, quoting=csv.QUOTE_NONE, error_bad_lines=False)
equi = pd.read_csv('acter_equi_relative-all.csv', delimiter = '\t', header = None, quoting=csv.QUOTE_NONE, error_bad_lines=False)
corp = pd.read_csv('acter_corp_relative-all.csv', delimiter = '\t', header = None, quoting=csv.QUOTE_NONE, error_bad_lines=False)
len(wind), len(equi),len(corp)
train = pd.concat([wind, equi, corp]).rename(columns={0:'words',1:'term_score',2:'id'})
# train.to_csv('acter_train_relative-all.csv')

In [3]:
train_dict = pd.Series(train['term_score'].values,index=train['words']).to_dict()
# train_dict

In [4]:
import json

with open('term_score_dict.json', 'w') as fp:
    json.dump(train_dict, fp)

In [5]:
class KeyTerm():
    def __init__(self, train_dict_dir = 'term_score_dict.json', data_dir = "../ACTER", language = 'en', term = "equi", nes=False):
        data_file = os.path.join(data_dir, language, term, 'annotations')
        self.nlp = stanza.Pipeline(lang='en')
        with open(train_dict_dir, 'r') as fp: 
            self.dicts = json.load(fp)

    
    def lemma(self, doc):
        lemma_word = self.nlp(str(doc))
        lemma_word = ' '.join([w.lemma for sent in lemma_word.sentences for w in sent.words])
        lemma_word = re.sub(' -','-',lemma_word)
        lemma_word = re.sub('- ','-',lemma_word)
        lemma_word = re.sub(' -','-',lemma_word)
        lemma_word = re.sub('- ','-',lemma_word)
        lemma_word = re.sub('/ ','/',lemma_word)
        lemma_word = re.sub(' /','/',lemma_word)
        lemma_word = re.sub(' \)', ' ',lemma_word)
        lemma_word = re.sub('\( ', ' ',lemma_word)
        lemma_word = re.sub(' +', ' ',lemma_word)
        return lemma_word
    
    def extract_doc(self, doc, use_lemma=True):
        doc = self.nlp(doc)
        results = []
        for sent in doc.sentences:
            if use_lemma:
                lemma_word = ' '.join([w.lemma for w in sent.words])

                tokens = lemma_word.split()
                text = sent.text
            else:
                tokens = [token.text for token in sent.tokens]
                text = sent.text

            label = self.extract(tokens, text=text)

            
            results.append({
                "tokens": tokens,
                "sent": sent.text,
                "labels": label
            })
        return results

    def extract(self, tokens, text = None):
        if text == None:
            text = ' '.join(tokens)
        z = [0] * len(tokens)
        for i, token in enumerate(tokens):
            z[i] = self.dicts.get(self.lemma(token),0)
            print(self.lemma(token), z[i])
        return z

class ActerDataset():
    def __init__(self, data_dir = "../ACTER", language = 'en', nes=False):
        if language == 'en':
            nlp = spacy.load("en_core_web_sm")
        elif language == 'fr':
            nlp = spacy.load("fr_core_news_sm")
        elif language == 'nl':
            nlp = spacy.load("nl_core_news_sm")
        self.sentences = []
        self.labels = []
        self.tokens = []

        language_dir = os.path.join(data_dir, language)
        for term in ['corp','equi','wind']:
            keyterm = KeyTerm(data_dir = data_dir, language=language, term = term, nes=nes)

            sentences, labels, tokens = self.extract_term(language_dir, term, keyterm, nlp)

            self.sentences.extend(sentences)
            self.labels.extend(labels)
            self.tokens.extend(tokens)

    def extract_term(self, data_dir, term, keyterm, nlp):
        data_dir = os.path.join(data_dir, term, 'texts', "annotated")
        sentences = []
        labels = []
        all_token = []
        terms = []
        for file in os.listdir(data_dir):
            if file.endswith('.txt') and file.startswith(term):
                data_file = os.path.join(data_dir, file)
                print(data_file)
                with open(data_file) as f:
                    for line in f:
                        results = keyterm.extract_doc(line.strip().lower(), use_lemma=True)
                        for result in results:
#                             if set(result['labels']) != {'O'}:
                            sentences.append(result['sent'])
                            labels.append(result['labels'])
                            all_token.append(result['tokens'])

        return sentences, labels, all_token 

In [6]:
dataset = ActerDataset()
path = "../processed_data/en/"
if not os.path.exists(path):
        os.mkdir(path) 
with open(path + "ann_train_inl.pkl", "wb") as output_file:
    pickle.dump((dataset.sentences, dataset.labels, dataset.tokens), output_file)

2021-06-02 22:12:47 INFO: Loading these models for language: en (English):
| Processor | Package   |
-------------------------
| tokenize  | combined  |
| pos       | combined  |
| lemma     | combined  |
| depparse  | combined  |
| sentiment | sstplus   |
| ner       | ontonotes |

2021-06-02 22:12:47 INFO: Use device: cpu
2021-06-02 22:12:47 INFO: Loading: tokenize
2021-06-02 22:12:47 INFO: Loading: pos
2021-06-02 22:12:47 INFO: Loading: lemma
2021-06-02 22:12:47 INFO: Loading: depparse
2021-06-02 22:12:48 INFO: Loading: sentiment
2021-06-02 22:12:48 INFO: Loading: ner
2021-06-02 22:12:49 INFO: Done loading processors!


../ACTER/en/corp/texts/annotated/corp_en_19.txt
unite 0
nation 0.0
convention 0.4398026678234647
against 0.0
corruption 0.5587929036987209
this 0.0
decision 0.3139108309194478
authorise 0.3612903986861538
the 0.0
president 0.2177050767998182
of 0.0
the 0.0
council 0.3075889247895641
to 0.0
designate 0.3240505749789996
the 0.0
person 0.3345239966539031
empower 0.3219029941644557
to 0.0
sign 0.2180012953443972
the 0.0
unite 0
nation 0.0
convention 0.4398026678234647
against 0.0
corruption 0.5587929036987209
on 0.0
behalf 0.269775776524128
of 0.0
the 0.0
european 0.3559879458447258
community 0.2970300228728608
. 0.0
the 0.0
convention 0.4398026678234647
aim 0.2732479533375487
to 0.0
boost 0.1936827805785477
the 0.0
effectiveness 0.3345072647001977
of 0.0
the 0.0
fight 0.3029379410143093
against 0.0
corruption 0.5587929036987209
, 0.0
promote 0.2604965259145518
the 0.0
proper 0.2148882926763663
management 0.2809302239540309
of 0.0
public 0.3458407194697094
affair 0.2392875010523473
and 0.0

accountability 0.3450927039624269
and 0.0
proper 0.2148882926763663
management 0.2809302239540309
of 0.0
public 0.3458407194697094
affair 0.2392875010523473
and 0.0
public 0.3458407194697094
property 0.1811544787706597
. 0.0
it 0.0
apply 0.297495337033261
to 0.0
the 0.0
prevention 0.4200476460274484
, 0.0
investigation 0.3726910487533021
and 0.0
prosecution 0.3950845366745083
of 0.0
corruption 0.5587929036987209
and 0.0
to 0.0
the 0.0
freezing 0.3069226019114556
, 0.0
seizure 0.3447894648614548
, 0.0
confiscation 0.494756659827395
and 0.0
return 0.0539439089688658
of 0.0
the 0.0
proceed 0.294635670223263
of 0.0
offence 0.4300018947465832
. 0.0
the 0.0
convention 0.4398026678234647
enumerate 0.0
in 0.0
detail 0.1756192650209098
the 0.0
measure 0.3431337372413084
to 0.0
prevent 0.2885962787373238
corruption 0.5587929036987209
, 0.0
include 0.2650103509131016
the 0.0
application 0.2736132432064954
of 0.0
prevention 0.4200476460274484
policy 0.2754769850388504
and 0.0
practice 0.2765266497

measure 0.3431337372413084
concern 0.315850170440739
proceedings 0.3744427622270038
and 0.0
penalty 0.3991771366692468
against 0.0
public 0.3458407194697094
official 0.3563174003330001
, 0.0
so 0.0966497943555093
as 0.0
to 0.0
strike 0.096042101397481
a 0.0
balance 0.1903993763026992
between 0.0
they 0.0
immunity 0.3568804856705697
and 0.0
the 0.0
offence 0.4300018947465832
commit 0.3487382165301749
by 0.0
they 0.0
, 0.0
include 0.2650103509131016
the 0.0
ensue 0.0
consequence 0.222060207290825
. 0.0
the 0.0
convention 0.4398026678234647
devote 0.202140080689977
a 0.0
chapter 0.2272378578901226
to 0.0
international 0.2943756523943459
cooperation 0.471068222913543
. 0.0
the 0.0
state 0.2666300761128498
party 0.2966638308300643
be 0.0
to 0.0
cooperate 0.3982314504085216
on 0.0
criminal 0.4401345161878328
matter 0.2292201250377029
and 0.0
on 0.0
matter 0.2292201250377029
of 0.0
extradition 0.4335958933440305
and 0.0
transfer 0.2046154878290094
of 0.0
sentence 0.2135108032733445
person 0.3

corruption 0.5587929036987209
be 0.0
approve 0.2429612216564826
on 0.0
behalf 0.269775776524128
of 0.0
the 0.0
european 0.3559879458447258
community 0.2970300228728608
. 0.0
the 0.0
decision 0.3139108309194478
authorise 0.3612903986861538
the 0.0
president 0.2177050767998182
of 0.0
the 0.0
council 0.3075889247895641
to 0.0
designate 0.3240505749789996
the 0.0
person 0.3345239966539031
( 0.0
's 0.0
) 0.0
who 0.0
shall 0.0
be 0.0
empower 0.3219029941644557
to 0.0
deposit 0.2642428670460143
the 0.0
community 0.2970300228728608
's 0.0
instrument 0.3500893905108604
of 0.0
formal 0.2221930779644941
confirmation 0.0
. 0.0
this 0.0
instrument 0.3500893905108604
be 0.0
bind 0.2536498448739183
on 0.0
the 0.0
community 0.2970300228728608
. 0.0
it 0.0
consist 0.2185791633051973
of 0.0
a 0.0
declaration 0.4172565009126844
of 0.0
the 0.0
community 0.2970300228728608
's 0.0
competence 0.3305771012010132
regard 0.3139357530569284
matter 0.2292201250377029
that 0.0
be 0.0
govern 0.3180109256872495
by 0

...

order 0.2391622161183857
to 0.0
avoid 0.2245433421320707
shading 0.3733532044606585
cover 0.2767061102356764
the 0.0
reservation 0.385750558204256
territory 0.2862005300383855
in 0.0
morning 0.0
hour 0.0
, 0.0
it 0.0
be 0.0
necessary 0.3048916767372317
to 0.0
examine 0.2273136171029164
a 0.0
alternative 0.1570134322614677
to 0.0
move 0.0220083642098435
the 0.0
wps 0.0
farther 0.3309980930590148
from 0.0
the 0.0
boundary 0.0
of 0.0
the 0.0
reservation 0.385750558204256
) 0.0
. 0.0
2 0.0
. 0.0
the 0.0
administration 0.3326091149012215
of 0.0
the 0.0
kretinga 0.6902555800137892
district 0.1804920245465245
municipality 0.412635482367654
by 0.0
its 0.0
letter 0.1189258863963618
no 0.0
. 0.0
( 0.0
6.27 0.0
. 0.0
) 0.0
-d34228 0.0
of 0.0
08-12-2005 0.0
approve 0.2429612216564826
of 0.0
the 0.0
report 0.2959449040274161
. 0.0
3. 0.0
kretinga 0.6902555800137892
branch 0.1359060244151392
of 0.0
the 0.0
klaip 0.0
da 0.0
public 0.3458407194697094
health 0.0727840333468517
centre 0.1218347887707401

use 0.17438416989225
, 0.0
the 0.0
effective 0.3132105329360837
solution 0.2107901526764027
of 0.0
master 0.2581356256676457
plan 0.1806990975341998
and 0.0
special 0.2141173846035081
plan 0.1806990975341998
make 0.181890370405065
for 0.0
the 0.0
municipal 0.3610792632632129
territory 0.2862005300383855
or 0.0
its 0.0
part 0.2085982340433795
, 0.0
be 0.0
to 0.0
be 0.0
approve 0.2429612216564826
by 0.0
a 0.0
relevant 0.3381247301448404
municipal 0.3610792632632129
council 0.3075889247895641
. 0.0
law 0.3276847867851072
no 0.0
. 0.0
i- 0.0
1120 0.0
of 0.0
the 0.0
republic 0.2356499019596868
of 0.0
lithuania 0.2959624002312053
on 0.0
zoning 0.6864100952495747
, 0.0
date 0.2112355629101935
12 0.0
december 0.2761403965232415
1995 0.0
. 0.0
order 0.2391622161183857
no 0.0
. 0.0
d1-239 0.0
of 0.0
the 0.0
minister 0.1567678739734828
of 0.0
environment 0.1473460767076944
of 0.0
the 0.0
republic 0.2356499019596868
of 0.0
lithuania 0.2959624002312053
on 0.0
approval 0.2748676099831925
of 0.0
the 

. 0.0
the 0.0
meeting 0.221643181685807
be 0.0
announce 0.1380095126811548
in 0.0
the 0.0
regional 0.3281184945341494
newspaper 0.0
" 0.0
svytury 0
" 0.0
( 0.0
no . 0
35 0.0
( 0.0
7764 0.0
) 0.0
) 0.0
on 0.0
may 0.2311584644228791
10 0.0
, 0.0
2006 0.0
. 0.0
no 0.0
planning 0.652096670586429
suggestion 0.1993344882255563
or 0.0
objection 0.0
from 0.0
the 0.0
public 0.3458407194697094
be 0.0
receive 0.244811748487956
at 0.0
the 0.0
meeting 0.221643181685807
. 0.0
the 0.0
meeting 0.221643181685807
be 0.0
hold 0.1812167693080161
in 0.0
klaipeda 0.6489290062918561
county 0.1505352217383042
municipality 0.412635482367654
. 0.0
the 0.0
planning 0.652096670586429
manager 0.1835946419808657
( 0.0
kretinga 0.6902555800137892
county 0.1505352217383042
municipality 0.412635482367654
manager 0.1835946419808657
) 0.0
valerijone 0
erneckis 0.0
, 0.0
senior 0.0
architect 0.0
of 0.0
kretinga 0.6902555800137892
county 0.1505352217383042
municipality 0.412635482367654
department 0.2572629788705504
of 0.

by 0.0
the 0.0
company 0.2100451779682594
of 0.0
the 0.0
agreement 0.276913817291884
on 0.0
transfer 0.2046154878290094
of 0.0
detailed 0.2547238335823028
planning 0.652096670586429
organizer 0.0
rights 0.2376883462015591
with 0.0
the 0.0
kretinga 0.6902555800137892
district 0.1804920245465245
municipality 0.412635482367654
( 0.0
director 0.2103235669313434
of 0.0
administration 0.3326091149012215
of 0.0
the 0.0
municipality 0.412635482367654
) 0.0
as 0.0
the 0.0
formal 0.2221930779644941
organizer 0.0
of 0.0
the 0.0
planning 0.652096670586429
, 0.0
on 0.0
5 0.0
august 0.1583335021929174
2004 0.0
. 0.0
in 0.0
the 0.0
process 0.232664718945309
of 0.0
territory 0.2862005300383855
detailed 0.2547238335823028
plan 0.1806990975341998
the 0.0
various 0.2631946050408422
sanitary 0.3398255099497048
protection 0.3668043887086282
zone 0.0
of 0.0
the 0.0
wind 0.0
power 0.2035426851960664
station 0.2795882610615324
range 0.178879749057405
from 0.0
120 0.0
m 0.0
to 0.0
300 0.0
m 0.0
from 0.0
the 0.

plan 0.1806990975341998
take 0.2014124842324145
place 0.1876777215779387
on 0.0
may 0.2311584644228791
22 0.0
, 0.0
2006 0.0
. 0.0
the 0.0
meeting 0.221643181685807
be 0.0
announce 0.1380095126811548
in 0.0
the 0.0
regional 0.3281184945341494
newspaper 0.0
" 0.0
svytury 0
" 0.0
( 0.0
no . 0
35 0.0
( 0.0
7764 0.0
) 0.0
) 0.0
on 0.0
may 0.2311584644228791
10 0.0
, 0.0
2006 0.0
. 0.0
no 0.0
planning 0.652096670586429
suggestion 0.1993344882255563
or 0.0
objection 0.0
from 0.0
the 0.0
public 0.3458407194697094
be 0.0
receive 0.244811748487956
at 0.0
the 0.0
meeting 0.221643181685807
or 0.0
by 0.0
the 0.0
address 0.269229078307596
mention 0.2332017673571871
in 0.0
the 0.0
newspaper 0.0
. 0.0
the 0.0
meeting 0.221643181685807
be 0.0
hold 0.1812167693080161
at 0.0
the 0.0
county 0.1505352217383042
municipality 0.412635482367654
of 0.0
kretinga 0.6902555800137892
. 0.0
the 0.0
planning 0.652096670586429
manager 0.1835946419808657
dainius 0.6198084771965466
jurena 0
, 0.0
secretary 0.1626149459

In [7]:
train = ['../processed_data/en/ann_train_inl.pkl']
train_df = pd.DataFrame(columns=["sentence_id", "words", "labels"])
final_train_df = pd.DataFrame()

for i in train:
    with open(i, "rb") as input_file:
        sentences, labels, tokens = pickle.load(input_file)
    sentence_id = []
    words = []
    targets = []

    for index, (token, label) in tqdm(enumerate(zip(tokens, labels))):
        for t, l in zip(token, label):
            sentence_id.append(index)
            words.append(t)
            targets.append(l)
    train_df['sentence_id'] = sentence_id
    train_df['words'] = words
    train_df['labels'] = targets
    final_train_df = final_train_df.append(train_df, ignore_index=True)

print(final_train_df.labels.value_counts())
final_train_df.to_csv('../processed_data/en/ann_train_inl.csv', index=False)

7715it [00:00, 72426.95it/s]


0.000000    102037
0.485077      1270
0.270766       711
0.174647       506
0.558793       489
             ...  
0.555403         1
0.320532         1
0.333692         1
0.462634         1
0.225786         1
Name: labels, Length: 2735, dtype: int64


In [8]:
final_train_df

sentence_id       words    labels
0                 0      united  0.000000
1                 0      nation  0.000000
2                 0  convention  0.439803
3                 0     against  0.000000
4                 0  corruption  0.558793
...             ...         ...       ...
169336         7714           ,  0.000000
169337         7714      format  0.233211
169338         7714          or  0.000000
169339         7714        font  0.398153
169340         7714           .  0.000000

[169341 rows x 3 columns]

In [9]:
final_train_df[final_train_df.labels <= 0]

sentence_id     words  labels
0                 0    united     0.0
1                 0    nation     0.0
3                 0   against     0.0
5                 1      this     0.0
8                 1       the     0.0
...             ...       ...     ...
169333         7714  headings     0.0
169334         7714        or     0.0
169336         7714         ,     0.0
169338         7714        or     0.0
169340         7714         .     0.0

[102037 rows x 3 columns]

In [10]:
final_train_df[final_train_df['words'] == 'states']

sentence_id   words   labels
28720           930  states  0.26663
51266          1866  states  0.26663
60093          2303  states  0.26663
60147          2305  states  0.26663
60417          2321  states  0.26663
60426          2321  states  0.26663
61555          2379  states  0.26663
62412          2429  states  0.26663
62769          2448  states  0.26663
62976          2454  states  0.26663
63128          2462  states  0.26663
63543          2481  states  0.26663
63558          2481  states  0.26663
63842          2492  states  0.26663
65593          2560  states  0.26663
67064          2633  states  0.26663
77891          3181  states  0.26663
77897          3181  states  0.26663
78359          3212  states  0.26663
114549         5062  states  0.26663
114555         5063  states  0.26663
114653         5064  states  0.26663
114678         5065  states  0.26663
115622         5111  states  0.26663
115713         5116  states  0.26663
116610         5160  states  0.26663
118444         5258  states  0.26663

In [11]:
print(len(train_df[train_df['words'] == 'states']))
print(len(train_df[train_df['words'] == 'state']))
train_df[train_df['words'] == 'states']

27
412


sentence_id   words   labels
28720           930  states  0.26663
51266          1866  states  0.26663
60093          2303  states  0.26663
60147          2305  states  0.26663
60417          2321  states  0.26663
60426          2321  states  0.26663
61555          2379  states  0.26663
62412          2429  states  0.26663
62769          2448  states  0.26663
62976          2454  states  0.26663
63128          2462  states  0.26663
63543          2481  states  0.26663
63558          2481  states  0.26663
63842          2492  states  0.26663
65593          2560  states  0.26663
67064          2633  states  0.26663
77891          3181  states  0.26663
77897          3181  states  0.26663
78359          3212  states  0.26663
114549         5062  states  0.26663
114555         5063  states  0.26663
114653         5064  states  0.26663
114678         5065  states  0.26663
115622         5111  states  0.26663
115713         5116  states  0.26663
116610         5160  states  0.26663
118444         5258  states  0.26663

In [12]:
train_df[train_df['words'] == 'states']

sentence_id   words   labels
28720           930  states  0.26663
51266          1866  states  0.26663
60093          2303  states  0.26663
60147          2305  states  0.26663
60417          2321  states  0.26663
60426          2321  states  0.26663
61555          2379  states  0.26663
62412          2429  states  0.26663
62769          2448  states  0.26663
62976          2454  states  0.26663
63128          2462  states  0.26663
63543          2481  states  0.26663
63558          2481  states  0.26663
63842          2492  states  0.26663
65593          2560  states  0.26663
67064          2633  states  0.26663
77891          3181  states  0.26663
77897          3181  states  0.26663
78359          3212  states  0.26663
114549         5062  states  0.26663
114555         5063  states  0.26663
114653         5064  states  0.26663
114678         5065  states  0.26663
115622         5111  states  0.26663
115713         5116  states  0.26663
116610         5160  states  0.26663
118444         5258  states  0.26663

In [14]:
import stanza

nlp = stanza.Pipeline(lang='en', processors='tokenize,mwt,pos,lemma')
doc = nlp('united nations winmech-loss effectiveness.')
print(*[f'word: {word.text+" "}\tlemma: {word.lemma}' for sent in doc.sentences for word in sent.words], sep='\n')

2021-06-03 11:39:34 WARNING: Can not find mwt: default from official model list. Ignoring it.
2021-06-03 11:39:34 INFO: Loading these models for language: en (English):
| Processor | Package  |
------------------------
| tokenize  | combined |
| pos       | combined |
| lemma     | combined |

2021-06-03 11:39:34 INFO: Use device: cpu
2021-06-03 11:39:34 INFO: Loading: tokenize
2021-06-03 11:39:34 INFO: Loading: pos
2021-06-03 11:39:35 INFO: Loading: lemma
2021-06-03 11:39:35 INFO: Done loading processors!


word: united 	lemma: unite
word: nations 	lemma: nation
word: winmech 	lemma: winmech
word: - 	lemma: -
word: loss 	lemma: loss
word: effectiveness 	lemma: effectiveness
word: . 	lemma: .
